In [1]:
import sys, os
from pymongo import MongoClient

from plotly.offline import init_notebook_mode, iplot
from plotly.graph_objs import *

from IPython.display import HTML, display

# https://stackoverflow.com/questions/41323423/plotly-inside-jupyter-notebook-python
init_notebook_mode(connected=True) # initiate notebook for offline plot

import pandas as pd
from datetime import datetime, timezone, timedelta

In [2]:
sys.path.append("..")
import config # ../config.py

# run on dellxps
config.mongodb_ip = "192.168.1.114"

client = MongoClient(host=config.mongodb_ip, port=config.mongodb_port)
db = client['steam']

## Collection Last Updated Time Deltas

In [3]:
apps_last_date = pd.DataFrame(list(db['apps'].find({}, {"updated_date":1, "_id":False}).sort([("updated_date",-1)]).limit(1)))['updated_date'][0].to_pydatetime().replace(tzinfo=timezone.utc)
pricehistory_last_date = pd.DataFrame(list(db['pricehistory'].find({}, {"date":1, "_id":False}).sort([("date",-1)]).limit(1)))['date'][0].to_pydatetime().replace(tzinfo=timezone.utc)
steamusers_last_date = pd.DataFrame(list(db['steamusers'].find({}, {"date":1, "_id":False}).sort([("date",-1)]).limit(1)))['date'][0].to_pydatetime().replace(tzinfo=timezone.utc)
topgames_last_date = pd.DataFrame(list(db['topgames'].find({}, {"date":1, "_id":False}).sort([("date",-1)]).limit(1)))['date'][0].to_pydatetime().replace(tzinfo=timezone.utc)
opencritic_last_date = pd.DataFrame(list(db['opencritic'].find({}, {"date":1, "_id":False}).sort([("date",-1)]).limit(1)))['date'][0].to_pydatetime().replace(tzinfo=timezone.utc)
twitchhistorical_last_date = pd.DataFrame(list(db['twitchhistorical'].find({}, {"date":1, "_id":False}).sort([("date",-1)]).limit(1)))['date'][0].to_pydatetime().replace(tzinfo=timezone.utc)

# https://stackoverflow.com/questions/6574329/how-can-i-produce-a-human-readable-difference-when-subtracting-two-unix-timestam
t = (datetime.now(timezone.utc) - apps_last_date).seconds
print('apps collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))
t = (datetime.now(timezone.utc) - pricehistory_last_date).seconds
print('pricehistory collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))
t = (datetime.now(timezone.utc) - steamusers_last_date).seconds
print('steamusers collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))
t = (datetime.now(timezone.utc) - topgames_last_date).seconds
print('topgames collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))
t = (datetime.now(timezone.utc) - opencritic_last_date).seconds
print('opencritic collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))
t = (datetime.now(timezone.utc) - twitchhistorical_last_date).seconds
print('twitchhistorical collection last updated: %d hours, %d minutes, %d seconds ago' % (t//3600, t%3600//60, t%60))

apps collection last updated: 0 hours, 44 minutes, 22 seconds ago
pricehistory collection last updated: 0 hours, 10 minutes, 14 seconds ago
steamusers collection last updated: 4 hours, 50 minutes, 1 seconds ago
topgames collection last updated: 0 hours, 3 minutes, 55 seconds ago
opencritic collection last updated: 0 hours, 35 minutes, 40 seconds ago
twitchhistorical collection last updated: 14 hours, 5 minutes, 34 seconds ago


## Number of Steam users online

In [4]:
pastday = datetime.today() - timedelta(days=90)
all_users_df = pd.DataFrame(list(db['steamusers'].find({"date": {"$gte": pastday}}, {"date":1, "numberonlineusers":1, '_id':False})))
all_users_df

date  numberonlineusers
0     2022-04-22 17:17:38           25475922
1     2022-04-22 17:18:01           25468992
2     2022-04-22 17:22:24           25395491
3     2022-04-22 17:22:46           25389310
4     2022-04-22 17:27:09           25314867
...                   ...                ...
59953 2022-07-21 18:06:20           23287630
59954 2022-07-21 18:11:06           23245523
59955 2022-07-21 18:15:52           23200867
59956 2022-07-21 18:20:38           23144804
59957 2022-07-21 18:25:24           23081941

[59958 rows x 2 columns]

In [5]:
# https://plot.ly/python/line-charts/

data = [Scatter(
        x=all_users_df['date'],
        y=all_users_df['numberonlineusers']
    )]

layout = Layout(
        title='Number of Steam users online over the past 90 days',
        xaxis=dict(
            title='Date'
        ),
        yaxis=dict(
            title='Number of Users'
        )
    )

fig = Figure(data=data, layout=layout)

iplot(fig)

## Top 50 Steam Games By Number of Recommendations

In [6]:
recommendations_df = pd.DataFrame(list(
    db['apps'].aggregate([
        {'$match': {"recommendations.total": {"$exists":True}}},
        {"$project": {"_id": False, "appid": 1, "name": 1, "steam_recommendations": "$recommendations.total"}}
    ])
)).sort_values(by='steam_recommendations', ascending=False).head(50)

recommendations_df

name    appid  steam_recommendations
25      Counter-Strike: Global Offensive      730                3404344
6753                 PUBG: BATTLEGROUNDS   578080                1613428
2343                  Grand Theft Auto V   271590                1231109
3904      Tom Clancy's Rainbow Six Siege   359550                 890285
993                             Terraria   105600                 766125
121                          Garry's Mod     4000                 709358
1971                                Rust   252490                 642608
2691            The Witcher 3: Wild Hunt   292030                 585645
9306                            Among Us   945360                 548077
5067                    Wallpaper Engine   431960                 478160
12867                     Cyberpunk 2077  1091500                 457411
21                         Left 4 Dead 2      550                 443179
3657               ARK: Survival Evolved   346110                 430179
4276                    Dead by Daylight   381210                 428990
1502              Euro Truck Simulator 2   227300                 422030
1987                       Rocket League   252950                 414274
10348                          Fall Guys  1097150                 404354
4798                      Stardew Valley   413150                 402119
13715                         ELDEN RING  1245620                 386754
1344                            PAYDAY 2   218620                 369522
11584                       Phasmophobia   739630                 357672
1738                          The Forest   242760                 314930
9172                             Valheim   892970                 300173
1388                                DayZ   221100                 255366
11171              Red Dead Redemption 2  1174180                 251081
1692                         Dying Light   239140                 239245
23                              Portal 2      620                 238934
3236               Don't Starve Together   322330                 224109
6799               Monster Hunter: World   582010                 219419
4163                     DARK SOULS™ III   374320                 214022
4052                       Hollow Knight   367520                 210213
11984                     Sea of Thieves  1172620                 195616
11233                          New World  1063730                 195453
2415                        No Man's Sky   275850                 184916
1920       The Binding of Isaac: Rebirth   250900                 182418
2215                          Subnautica   264710                 180822
913          The Elder Scrolls V: Skyrim    72850                 179173
786                        Borderlands 2    49520                 179116
3231                       Geometry Dash   322170                 176881
12739              鬼谷八荒 Tale of Immortal  1468810                 176730
4210                           Fallout 4   377160                 176515
10715                              Hades  1145360                 174310
9868   Halo: The Master Chief Collection   976730                 172009
1000                              Arma 3   107410                 167857
9563                         Bloons TD 6   960090                 167429
4443                           Undertale   391540                 159032
2626         Sid Meier's Civilization VI   289070                 157711
1937                       7 Days to Die   251570                 154740
7435                                Raft   648800                 148787
11690       Mount & Blade II: Bannerlord   261550                 148262

## Count of apps by type

In [7]:
display(HTML((pd.DataFrame(list(
    db['apps'].aggregate([
        {"$group" : {"_id":"$type", "count":{"$sum":1}}}
    ])
)).sort_values(by='count', ascending=False).to_html())))

print("Total apps: " + str(db['apps'].count_documents({})))

Total apps: 157793
